<a href="https://colab.research.google.com/github/allakutkina/eggsplain/blob/main/Explainability_in_BERT_for_Humor_Detection.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install transformers

In [ ]:
!pip install bertviz

In [ ]:
!pip install transformers-interpret

In [ ]:
!pip install imgkit

In [ ]:
!pip install shap

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 547.9/547.9 kB 4.0 MB/s eta 0:00:00


In [ ]:
!pip install LIME

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
model_save_path = '/content/drive/MyDrive/RedditHumorDetection/final_results_puns/'
train_data_path = '/content/drive/MyDrive/RedditHumorDetection/data/puns/train.tsv'
dev_data_path = '/content/drive/MyDrive/RedditHumorDetection/data/puns/dev.tsv'

# Define training parameters, following "Transformers get the last laugh"
batch_size = 256
learning_rate = 2e-5
num_epochs = 7
# we reduce max size from 128 because our longest sequence is 45 words, 64 tokens is more then sufficient
max_len = 64

In [ ]:
#imports
import torch
import pandas as pd
import numpy as np
from transformers import BertTokenizer, BertForSequenceClassification, get_linear_schedule_with_warmup
from torch.utils.data import DataLoader, TensorDataset, random_split
from torch.optim import AdamW

In [ ]:
#set the (GPU) device
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
print(torch.cuda.is_available())

True


In [ ]:
# Load and preprocess training data
train_data = pd.read_csv(train_data_path, sep=',', header=None, names=['ID', 'Label', 'Sub', 'Text'])
dev_data = pd.read_csv(dev_data_path, sep=',', header=None, names=['ID', 'Label', 'Sub', 'Text'])
# Tokenize and encode the text data
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

train_texts = tokenizer(train_data['Text'].tolist(), padding=True, truncation=True, return_tensors='pt', max_length=max_len)
dev_texts = tokenizer(dev_data['Text'].tolist(), padding=True, truncation=True, return_tensors='pt', max_length=max_len)
# Create PyTorch tensors for input data
input_ids_t, attention_mask_t, labels_t = train_texts['input_ids'], train_texts['attention_mask'], torch.tensor(train_data['Label'].tolist())
input_ids_d, attention_mask_d, labels_d = dev_texts['input_ids'], dev_texts['attention_mask'], torch.tensor(dev_data['Label'].tolist())

# Create DataLoader for training and validation sets

train_dataset = TensorDataset(input_ids_t, attention_mask_t, labels_t)
train_loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True)

val_dataset = TensorDataset(input_ids_d, attention_mask_d, labels_d)
val_loader = DataLoader(val_dataset, batch_size=batch_size)


FileNotFoundError: ignored

In [ ]:
# Load the model
model = BertForSequenceClassification.from_pretrained('bert-base-uncased', num_labels=2, output_attentions = True)

#set optimiser and sceduler
optimizer = AdamW(model.parameters(), lr=learning_rate)
scheduler = get_linear_schedule_with_warmup(optimizer, num_warmup_steps=0, num_training_steps=len(train_loader) * num_epochs)

# Move the model to the GPU
model.to(device)

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


BertForSequenceClassification(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(30522, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0-11): 12 x BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e-12,

#Training

## Parameter experiment

In [ ]:
#setting all the parameters untrainable up to last layer
'''
i=0
for param in model.parameters():
    if i < 11:
      param.requires_grad = False
    else:
      param.requires_grad = True
    print(param.shape)
    print(param.requires_grad)
    if param.shape == torch.Size([3072]):
        i+=1
        print(i)
'''

In [ ]:
#setting all the parameters untrainable except the first layer + embeddings
'''
i=0
for param in model.parameters():
    if i < 1:
      param.requires_grad = True
    else:
      param.requires_grad = False
    print(param.shape)
    print(param.requires_grad)
    if param.shape == torch.Size([3072]):
        i+=1
        print(i)
'''

## Actual training

In [ ]:
# Training loop
for epoch in range(num_epochs):
    model.train()
    total_loss = 0
    val_loss = 0
    correct_val = 0
    total_val = 0
    for batch in train_loader:
        input_ids, attention_mask, labels = batch
        input_ids, attention_mask, labels = input_ids.to(device), attention_mask.to(device), labels.to(device)

        optimizer.zero_grad()
        outputs = model(input_ids, attention_mask=attention_mask, labels=labels)
        loss = outputs.loss
        loss.backward()
        optimizer.step()
        scheduler.step()

        total_loss += loss.item()

    # Calculate average loss for this epoch
    avg_loss = total_loss / len(train_loader)
    print(f"Epoch {epoch + 1}/{num_epochs} - Average Loss: {avg_loss:.4f}")

    with torch.no_grad():
        for batch in val_loader:
            input_ids, attention_mask, labels = batch
            input_ids, attention_mask, labels = input_ids.to(device), attention_mask.to(device), labels.to(device)

            outputs = model(input_ids, attention_mask=attention_mask, labels=labels)
            loss = outputs.loss
            val_loss += loss.item()

            # Calculate accuracy
            _, predicted = torch.max(outputs.logits, 1)
            correct_val += (predicted == labels).sum().item()
            total_val += labels.size(0)

    avg_val_loss = val_loss / len(val_loader)
    val_accuracy = correct_val / total_val


    print(f"Epoch {epoch + 1}/{num_epochs} - Train Loss: {avg_loss:.4f} - Val Loss: {avg_val_loss:.4f} - Val Accuracy: {val_accuracy:.4f}")

# Save the fine-tuned model
model.save_pretrained(model_save_path)

Epoch 1/7 - Average Loss: 0.5546
Epoch 1/7 - Train Loss: 0.5546 - Val Loss: 0.4389 - Val Accuracy: 0.8242
Epoch 2/7 - Average Loss: 0.3332
Epoch 2/7 - Train Loss: 0.3332 - Val Loss: 0.3394 - Val Accuracy: 0.8673
Epoch 3/7 - Average Loss: 0.2420
Epoch 3/7 - Train Loss: 0.2420 - Val Loss: 0.3041 - Val Accuracy: 0.8872
Epoch 4/7 - Average Loss: 0.1858
Epoch 4/7 - Train Loss: 0.1858 - Val Loss: 0.2941 - Val Accuracy: 0.8872
Epoch 5/7 - Average Loss: 0.1620
Epoch 5/7 - Train Loss: 0.1620 - Val Loss: 0.2899 - Val Accuracy: 0.8889
Epoch 6/7 - Average Loss: 0.1292
Epoch 6/7 - Train Loss: 0.1292 - Val Loss: 0.2996 - Val Accuracy: 0.8905
Epoch 7/7 - Average Loss: 0.1274
Epoch 7/7 - Train Loss: 0.1274 - Val Loss: 0.2916 - Val Accuracy: 0.8988


## Helper methods

In [ ]:
# for reseting the moddel if necessary
#del(model)

In [ ]:
# method for predicting from preprocessed data
# Returns: predicted class label, attentions
def predict_with_attentions(input_ids, attention_mask):
    # Make predictions
    with torch.no_grad():
        outputs = model(input_ids, attention_mask=attention_mask)

    # Extract the attention scores from the model
    attentions = outputs['attentions']
    #print(attentions)
    #get predicted label
    logits = outputs.logits
    probabilities = torch.softmax(logits, dim=1)
    predicted_class = torch.argmax(probabilities, dim=1).item()
    predicted_class
    return predicted_class, attentions

In [ ]:
# method for predicting from raw text
# Returns: predicted label, attentions, tokenised sequence (tokenised sequence differs from input sentence due to subwords)
def predict_with_attentions_and_tokens(text):
    input_ids = tokenizer.encode(text, add_special_tokens=True, return_tensors='pt').to(device)
    # Make predictions
    with torch.no_grad():
        outputs = model(input_ids)

    # Extract the attention scores from the model
    attentions = outputs['attentions']
    #print(attentions)
    #get predicted label
    logits = outputs.logits
    probabilities = torch.softmax(logits, dim=1)
    predicted_class = torch.argmax(probabilities, dim=1).item()
    predicted_class
    return predicted_class, attentions, tokenizer.convert_ids_to_tokens(input_ids[0])

# Generate explanations for individual instances

In this section we generate explanations for one examplary instance in order to test our methods. The examplary instance chosen is:
- "highways today are much better than they were many years ago and there are lots of concrete examples of it"

which is an arbitrary chosen instance from Pun of The Day dataset

## BertViz

In [ ]:
#more imports
from pathlib import Path
from bertviz import model_view, head_view
from transformers_interpret import SequenceClassificationExplainer
import numpy as np

In [ ]:
sample_text  = "highways today are much better than they were many years ago and there are lots of concrete examples of it"
prediction, attentions, tokens = predict_with_attentions_and_tokens(sample_text)
print(f'{sample_text} \n label: {prediction}')
model_view_html = model_view(attentions, tokens, html_action='return')

highways today are much better than they were many years ago and there are lots of concrete examples of it 
 label: 0


In [ ]:
head_view(attentions, tokens, html_action='return')

We see that humorous examples have more attention towards the CLS token in later layers (head specific?)



We are interested in true predictions because the attention maps in true predictions supposed to capture the difference beteween positive and negative instances

Illustrate how attention patterns concentrate on cls token
Conclusion: classification will result in cls token being attended to the most since that's the token used in the prediction for classification task

##Transformers Interpret

In [ ]:
from transformers_interpret import SequenceClassificationExplainer
cls_explainer = SequenceClassificationExplainer(
    model,
    tokenizer)
word_attributions = cls_explainer("highways today are much better than they were many years ago and there are lots of concrete examples of it", class_name="LABEL_0")

In [ ]:
word_attributions

[('[CLS]', 0.0),
 ('highways', -0.3947688016478789),
 ('today', 0.3127786553034568),
 ('are', 0.005989683969161539),
 ('much', 0.08249703205555628),
 ('better', -0.023669276163820065),
 ('than', -0.07764450734115194),
 ('they', -0.1225244262623618),
 ('were', 0.09275974111523748),
 ('many', 0.0899328504200383),
 ('years', -0.010411086138553113),
 ('ago', -0.08639339655041903),
 ('and', 0.30878167251521993),
 ('there', 0.09303836304789652),
 ('are', 0.06811350521773381),
 ('lots', 0.15648061685228867),
 ('of', 0.05934471956313609),
 ('concrete', -0.443399540210971),
 ('examples', 0.3457555951418597),
 ('of', 0.1139777153217724),
 ('it', 0.4773145115241662),
 ('[SEP]', 0.0)]

In [ ]:
word_attributions = cls_explainer("highways today are much better than they were many years ago and there are lots of concrete examples of it", class_name="LABEL_1")
cls_explainer.visualize()

In [ ]:
word_attributions_neg = cls_explainer("highways today are much better than they were many years ago and there are lots of concrete examples of it", class_name="LABEL_0")
cls_explainer.visualize()

# LIME

In [ ]:
import matplotlib.pyplot as plt
import numpy as np


In [ ]:
from transformers import pipeline
pipe = pipeline("text-classification", model=model, tokenizer=tokenizer, device = device, return_all_scores =True)

`return_all_scores` is now deprecated,  if want a similar functionality use `top_k=None` instead of `return_all_scores=True` or `top_k=1` instead of `return_all_scores=False`.


In [ ]:
#wrapper around the pipe to get scores for lime

def score_out(text):
    inputs = tokenizer(text, return_tensors='pt', padding=True, truncation=True)
    input_ids = inputs['input_ids']
    attention_mask = inputs['attention_mask']
    input_ids, attention_mask = input_ids.to(device), attention_mask.to(device)
    with torch.no_grad():
        outputs = model(input_ids, attention_mask=attention_mask)
    logits = outputs.logits
    probabilities = torch.softmax(logits, dim=1)
    return np.asarray(probabilities.cpu())

In [ ]:
from lime import lime_text


from lime.lime_text import LimeTextExplainer
explainer = LimeTextExplainer(class_names=[0,1])
# num features is num tokens
num_features =  len(sample_text)
# number of samples to generate as prediction for local explanation. we have up to 45 words, how many samples makes sence? Every word changed at least once? would something like 45^2 suffise?
# set to default: seem to give more stable reslt then 45²
num_samples = 5000
exp = explainer.explain_instance(sample_text, score_out,labels=(1,), num_features = num_features, num_samples=num_samples)
exp.show_in_notebook()

# SHAP

In [ ]:
import shap
# define the explainer
explainer = shap.Explainer(pipe)

In [ ]:
shap_values = explainer(['highways today are much better than they were many years ago and there are lots of concrete examples of it'])
shap.plots.text(shap_values)

You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset


  0%|          | 0/462 [00:00<?, ?it/s]

Partition explainer: 2it [00:16, 16.25s/it]               


In [ ]:
#checking the exact type of explainer for future writing
type(explainer)

shap.explainers._partition.Partition

In [ ]:
shap_values

.values =
array([[[ 0.03362001, -0.03362001],
        [-0.32275885,  0.32275885],
        [ 0.02398176, -0.02398177],
        [ 0.04544645, -0.04544645],
        [ 0.13848006, -0.13848005],
        [ 0.11787977, -0.11787977],
        [ 0.00704534, -0.00704534],
        [ 0.00972766, -0.00972765],
        [ 0.03986787, -0.03986788],
        [ 0.05640318, -0.05640318],
        [-0.02583388,  0.02583387],
        [ 0.08562727, -0.08562726],
        [-0.0034096 ,  0.00340961],
        [ 0.05698887, -0.05698886],
        [-0.02018243,  0.02018242],
        [ 0.0519917 , -0.05199171],
        [ 0.02669627, -0.02669629],
        [-0.33545048,  0.33545048],
        [-0.10162281,  0.10162282],
        [ 0.02893476, -0.02893475],
        [ 0.14202129, -0.14202129],
        [-0.08630486,  0.08630484]]])

.base_values =
array([[0.45925382, 0.54074621]])

.data =
(array(['', ' highways', ' today', ' are', ' much', ' better', ' than',
       ' they', ' were', ' many', ' years', ' ago', ' and', ' the

train a model on a slot-filling task for minimal edits and get attentions. Most BERT-native form. Humicroedit

# Generating explanations for the dev set

We choose dev set because we didn't train on it but labels are acessible. We are avare that that is somewhat a biased way, because the amount of epocs was chosen based on dev set parameters. However, it is not strictly apeaking a selection of best model but rather an explainability experiment. Our question is not how well the model would perform on unseen data, but why the model makes the decision it makes.

In [ ]:
import os
from pathlib import Path

In [ ]:
with torch.no_grad():
    predictions_d = model(input_ids_d[:100].to(device), attention_mask_d[:100].to(device))


In [ ]:
#loop for generating individual explanations
#we loop through the data once to generate explanations with all 4 methods and then generate html files and images for each.
#first 100 instances from the dev set: the methods are computationally expensive

explainer_lime = LimeTextExplainer(class_names=[0,1])

explainer_shap = shap.Explainer(pipe)
id = 0

for input_ids, attention_mask, label, text in zip(input_ids_d[:100], attention_mask_d[:100], labels_d[:100], dev_data['Text'].tolist()[:100]):
    print(text)
    # predict
    predicted_label, attentions, tokens = predict_with_attentions_and_tokens(text)

    correct = bool(label==predicted_label)
    path = "/content/drive/MyDrive/BertExplained/"
    Path(path).mkdir(parents=True, exist_ok=True)

    # BertViz
    #length in the name of the file in case I will want to process/overlap pictures later
    length = len(input_ids.nonzero())
    model_view_html = model_view(attentions, tokens, html_action='return')
    header = f'<p>Text: {text}</p><p>Label: {label}</p><p>Predicted Label: {predicted_label}</p><p>Length: {length}</p>'
    path_bertviz = path + f"/{id}_{label}_{predicted_label}_{length}_bertviz.html"
    with open(path_bertviz, 'w') as file:
      file.write(header)
      file.write(model_view_html.data)

    # Transformers Interpret
    word_attributions = cls_explainer(text)
    pred_label = cls_explainer.pred_class
    path_html_TI = path  + f"/{id}_{label}_{pred_label}_TI.html"
    cls_explainer.visualize(path_html_TI, true_class=label)

    #LIME
    exp = explainer_lime.explain_instance(text, score_out,labels=(1,), num_features = length)
    html_LIME = exp.as_html()
    path_LIME = path + f"/{id}_{label}_LIME.html"
    with open(path_LIME, 'w') as file:
      file.write(html_LIME)

    #SHAP
    shap_values = explainer_shap([text])
    html_SHAP = shap.plots.text(shap_values, display=False)
    path_SHAP = path + f"/{id}_{label}_SHAP.html"
    with open(path_SHAP, 'w') as file:
        file.write(html_SHAP)

    id +=1


they served lunch at the auto repair shop but i didn t eat it it was full of carbs


You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset


  0%|          | 0/462 [00:00<?, ?it/s]

i was going to buy some loose tea but the price was too steep


You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset


...

  0%|          | 0/132 [00:00<?, ?it/s]

yesterday s high was 78 and the low was 45 but neither were records


You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset


the same way you want him to win your love


You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset


In [ ]:
import json

In [ ]:
#loop for obtaining numerical values

attributions=[]
lime_values = []


for input_ids, label, text in zip(input_ids_d[:100], labels_d[:100], dev_data['Text'].tolist()[:100]):
    length = len(input_ids.nonzero())

    # Transformers Interpret
    word_attributions = cls_explainer(text)
    pred_label = cls_explainer.pred_class
    attributions.append(word_attributions)

    #LIME
    exp = explainer_lime.explain_instance(text, score_out,labels=(1,), num_features = length)
    list_LIME = exp.as_list()
    lime_values.append(list_LIME)


#write to file


with open("/content/drive/MyDrive/BertExplained/TI.json", "w") as outfile:
    json.dump(attributions, outfile)

with open("/content/drive/MyDrive/BertExplained/LIME.json", "w") as outfile:
    json.dump(lime_values, outfile)


In [ ]:
#LIME generating images
id = 0
plt.rcParams['figure.figsize'] = [12, 8]
for input_ids, label, text in zip(input_ids_d[:100], labels_d[:100], dev_data['Text'].tolist()[:100]):
    length = len(input_ids.nonzero())
    #LIME
    exp = explainer_lime.explain_instance(text, score_out,labels=(1,), num_features = length)
    figure_LIME = exp.as_pyplot_figure()
    figure_LIME.suptitle(text)
    figure_LIME.savefig(f'/content/drive/MyDrive/BertExplained/{id}_{label}_LIME.jpg')
    id+=1


In [ ]:
#SHAP
shap_out = explainer_shap(dev_data['Text'].tolist()[:100])

In [ ]:
shap_out

In [ ]:
shap_list = []
for value, data in zip(shap_out.values, shap_out.data):
  shap_list.append([value.tolist(), data.tolist()])
with open("/content/drive/MyDrive/BertExplained/SHAP.json", "w") as outfile:
    json.dump(shap_list, outfile)